# Data extraction — load CSV from ZIP
This notebook demonstrates loading CSV files stored in `data/archive.zip` using the relative path `../data/archive.zip` (from the `jupyter_notebooks/` folder).

Notes:
- Make sure you open this notebook from the `jupyter_notebooks/` folder so the relative path works.
- The code below reads the CSV inside the ZIP into a pandas DataFrame.
- If the file is large, consider streaming or reading specific columns.

In [1]:
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut, GeocoderUnavailable
from collections import defaultdict
import time
from typing import Dict, Tuple

### Setup and imports

Initialize libraries and any options used by the ETL below.

In [2]:
# Load dataset from ZIP (relative to this notebook)
# ../data/archive.zip is resolved from jupyter_notebooks/ so it points to repo_root/data/archive.zip
# If the ZIP contains multiple CSVs, pandas will read the first; otherwise it reads the single CSV inside.
df = pd.read_csv('../data/archive.zip', compression='zip')

### Load data and quick checks

Load the dataset and show a quick shape/head to validate load.

In [3]:
df.head()

Unnamed: 0  State Code  County Code  Site Num  \
0           0           4           13      3002   
1           1           4           13      3002   
2           2           4           13      3002   
3           3           4           13      3002   
4           4           4           13      3002   

                                   Address    State    County     City  \
0  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
1  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
2  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
3  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
4  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   

   Date Local          NO2 Units  ...          SO2 Units  SO2 Mean  \
0  2000-01-01  Parts per billion  ...  Parts per billion  3.000000   
1  2000-01-01  Parts per billion  ...  Parts per billion  3.000000   
2  2000-01-01  Parts per billion  ...  Parts per billion  2.975000   
3  2000-01-01  Parts per billion  ...  Parts per billion  2.975000   
4  2000-01-02  Parts per billion  ...  Parts per billion  1.958333   

   SO2 1st Max Value  SO2 1st Max Hour SO2 AQI           CO Units   CO Mean  \
0                9.0                21    13.0  Parts per million  1.145833   
1                9.0                21    13.0  Parts per million  0.878947   
2                6.6                23     NaN  Parts per million  1.145833   
3                6.6                23     NaN  Parts per million  0.878947   
4                3.0                22     4.0  Parts per million  0.850000   

   CO 1st Max Value  CO 1st Max Hour CO AQI  
0               4.2               21    NaN  
1               2.2               23   25.0  
2               4.2               21    NaN  
3               2.2               23   25.0  
4               1.6               23    NaN  

[5 rows x 29 columns]

## Preview and inspect columns
The next cells preview the first rows (`df.head()`) and list all column names (`df.columns`) so we can confirm the schema before geocoding.

In [4]:
# List all columns to verify available geographic/address fields
# This helps ensure downstream grouping uses correct column names
# (Expected: Address, City, County, State; adjust if different)
df.columns

Index(['Unnamed: 0', 'State Code', 'County Code', 'Site Num', 'Address',
       'State', 'County', 'City', 'Date Local', 'NO2 Units', 'NO2 Mean',
       'NO2 1st Max Value', 'NO2 1st Max Hour', 'NO2 AQI', 'O3 Units',
       'O3 Mean', 'O3 1st Max Value', 'O3 1st Max Hour', 'O3 AQI', 'SO2 Units',
       'SO2 Mean', 'SO2 1st Max Value', 'SO2 1st Max Hour', 'SO2 AQI',
       'CO Units', 'CO Mean', 'CO 1st Max Value', 'CO 1st Max Hour', 'CO AQI'],
      dtype='object')

### Attempt 1: Heuristic geocoding anchored on the first address token
This section builds a coordinate dictionary by:
1. Extracting the first token of `Address` (treating it as an anchor / street number candidate).
2. Grouping by `(State, County, City, FirstToken)` to reduce duplicate geocode calls.
3. Geocoding each group and mapping the resulting (lat, lon) back to all member rows.

Important clarification:
- We are *anchoring* the query on the first token, not asserting the address only has that token. The remainder of the address is currently ignored in the query, which is why resolution quality drops for non‑numeric or ambiguous tokens.

Limitations of this approach:
- Non‑numeric starts (e.g. "Intersection", "PO", business names) yield vague queries.
- Different streets sharing the same leading number collapse into one geocode result (loss of specificity).
- Missing / inconsistent county values weaken the query.
- Ignoring the rest of the address means we discard potentially critical street names.

Next improvement (planned): incorporate the full normalized address with structured/fallback geocoding and cache results to reduce API calls.

In [5]:
# Geocoding setup and helper function
# Uses Nominatim (OpenStreetMap) with conservative retries.
# NOTE: High-volume geocoding against Nominatim should be rate-limited (1 req/sec).
# For production or bulk jobs, consider caching or other geocoding services.

# Setup geolocator (custom user_agent per usage policy)
geolocator = Nominatim(user_agent="daniel_validator_geocoder", timeout=10)

def safe_geocode(first_token, city, county, state, retries=3, delay=2):
    """
    Attempt geocode with exponential backoff on timeout/unavailable.
    first_token: heuristic partial address (e.g., street number or PO Box token).
    Returns (lat, lon) or (None, None).
    """
    query = f"{first_token}, {city}, {county} County, {state}"
    for i in range(retries):
        try:
            location = geolocator.geocode(query)
            if location:
                return (location.latitude, location.longitude)
        except (GeocoderTimedOut, GeocoderUnavailable):
            # Exponential backoff
            time.sleep(delay * (2 ** i))
    return (None, None)


### Geocoding helper setup

Define geocoding helpers and configuration used in subsequent attempts.

In [6]:
# Extract first token from Address (heuristic anchor). Examples:
#   '123 Main St' -> '123'
#   'PO Box 45' -> 'PO'
#   'Intersection of 5th and Pine' -> 'Intersection'
# This may miss specificity for non-numeric starts.
df["FirstToken"] = df["Address"].str.split().str[0]

# Group to reduce repeated geocode calls per token + city + county + state.
# NOTE: Over-grouping can merge unrelated addresses sharing identical first tokens.
grouped = df.groupby(["State", "County", "City", "FirstToken"])

# Prepare mapping: (lat, lon) → [indices] for later backfill into the dataframe.
coord_to_indices = defaultdict(list)

for group_keys, group_df in grouped:
    state, county, city, first_token = group_keys
    lat, lon = safe_geocode(first_token, city, county, state)
    if lat is not None and lon is not None:
        coord_to_indices[(lat, lon)].extend(group_df.index.tolist())

# Quick diagnostics: how many groups resolved vs total groups
resolved_groups = len(coord_to_indices)
all_groups = len(grouped)
print(f"Resolved groups: {resolved_groups} / {all_groups} ({resolved_groups/all_groups:.1%})")


Resolved groups: 138 / 203 (68.0%)


### Address tokenization (anchor)

Derive first token(s) from Address for initial geocoding anchors.

In [7]:
coord_to_indices

defaultdict(list,
            {(33.5206824, -86.8024326): [1329836,
              1329837,
              1329838,
              1329839,
              1329840,
              1329841,
              1329842,
              1329843,
              1329844,
              1329845,
              1329846,
              1329847,
              1329848,
              1329849,
              1329850,
              1329851,
              1329852,
              1329853,
              1329854,
              1329855,
              1329856,
              1329857,
              1329858,
              1329859,
              1329860,
              1329861,
              1329862,
              1329863,
              1329864,
              1329865,
              1329866,
              1329867,
              1329868,
              1329869,
              1329870,
              1329871,
              1329872,
              1329873,
              1329874,
              1329875,
              1329876,
            

In [8]:
len(coord_to_indices)

138

In [9]:
coord_to_indices.keys()

dict_keys([(33.5206824, -86.8024326), (33.6464627, -112.0951049), (33.5037055, -112.0135526), (33.4942189, -111.926018), (32.261343, -110.9921453), (32.226726, -110.935219), (34.7574314, -92.2814999), (37.8708393, -122.272863), (37.8044557, -122.271356), (38.0149216, -121.640508), (37.9768525, -122.0335624), (38.0525612, -122.2202603), (38.0181745, -121.8901232), (37.9621457, -122.3455263), (36.7558656, -119.7815872), (36.7817609, -119.7816083), (36.785134, -119.781587), (36.7334537, -119.5004303), (40.8018746, -124.1707558), (32.6668134, -115.4963754), (35.3738712, -119.019463), (34.1812089, -118.307201), (33.9128272, -118.3426122), (34.0149289, -118.2428023), (33.7690164, -118.191604), (34.6663688, -118.1603543), (33.8119936, -118.3823077), (33.8309043, -118.0897495), (34.0468546, -118.430254), (33.6633386, -117.903317), (33.9964933, -117.4079318), (38.6130409, -121.3687121), (34.0922947, -117.43433), (34.5361067, -117.2911565), (32.639838, -117.061831), (32.7947731, -116.962526), (3

In [10]:
# Optional: convert to DataFrame for inspection and export
coord_df = pd.DataFrame([
    {"Latitude": lat, "Longitude": lon, "Indices": indices, "count": len(indices)}
    for (lat, lon), indices in coord_to_indices.items()
]).sort_values("count", ascending=False)

# Show top locations that matched many rows (suspicious over-grouping)
coord_df.head(10)

Latitude   Longitude                                            Indices  \
6    34.757431  -92.281500  [634423, 634424, 634425, 634426, 634427, 63442...   
93   35.285598  -80.980301  [67172, 67173, 67174, 67175, 67176, 67177, 671...   
30   33.996493 -117.407932  [17730, 17731, 17732, 17733, 17734, 17735, 177...   
51   38.875384  -77.047032  [1127188, 1127189, 1127190, 1127191, 1127192, ...   
25   34.666369 -118.160354  [12130, 12131, 12132, 12133, 12134, 12135, 121...   
10   37.976852 -122.033562  [3516, 3517, 3518, 3519, 3520, 3521, 3522, 352...   
48   38.104086 -122.256637  [35400, 35401, 35402, 35403, 35404, 35405, 354...   
119  32.943742  -96.767500  [82530, 82531, 82532, 82533, 82534, 82535, 825...   
9    38.014922 -121.640508  [4968, 4969, 4970, 4971, 4972, 4973, 4974, 497...   
33   34.536107 -117.291156  [21134, 21135, 21136, 21137, 21138, 21139, 211...   

     count  
6    35332  
93   32012  
30   30178  
51   25696  
25   25225  
10   23686  
48   23678  
119  23406  
9    23396  
33   23279

In [11]:
coord_df

Latitude   Longitude                                            Indices  \
6    34.757431  -92.281500  [634423, 634424, 634425, 634426, 634427, 63442...   
93   35.285598  -80.980301  [67172, 67173, 67174, 67175, 67176, 67177, 671...   
30   33.996493 -117.407932  [17730, 17731, 17732, 17733, 17734, 17735, 177...   
51   38.875384  -77.047032  [1127188, 1127189, 1127190, 1127191, 1127192, ...   
25   34.666369 -118.160354  [12130, 12131, 12132, 12133, 12134, 12135, 121...   
..         ...         ...                                                ...   
76   38.728144  -90.387908  [60166, 60167, 60168, 60169, 60170, 60171, 601...   
17   36.733454 -119.500430  [285321, 285322, 285323, 285324, 285325, 28532...   
14   36.755866 -119.781587  [284501, 284502, 284503, 284504, 284505, 28450...   
20   35.373871 -119.019463  [10552, 10553, 10554, 10555, 10556, 10557, 105...   
128  40.299403 -109.988760  [1321376, 1321377, 1321378, 1321379, 1321380, ...   

     count  
6    35332  
93   32012  
30   30178  
51   25696  
25   25225  
..     ...  
76     860  
17     826  
14     820  
20     434  
128    104  

[138 rows x 4 columns]

In [12]:
sum(len(indices) for indices in coord_to_indices.values())

1375287

In [13]:
len(df)

1746661

Invert the Dictionary

In [15]:
# Flatten the dictionary: index → coordinate
index_to_coord = {
    idx: coord
    for coord, indices in coord_to_indices.items()
    for idx in indices
}

Create a Series and Join

In [16]:
# Backfill coordinates into df
# Map each row index to a (lat, lon) chosen from coord_to_indices
index_to_coord = {
    idx: coord
    for coord, indices in coord_to_indices.items()
    for idx in indices
}

# Safe fallback for missing entries
df['coord'] = df.index.map(lambda idx: index_to_coord.get(idx, (np.nan, np.nan)))

# Unpack safely
df[['x', 'y']] = pd.DataFrame(df['coord'].tolist(), index=df.index)
df.drop(columns='coord', inplace=True)

# Report how many rows remain unresolved
unresolved = df['x'].isna().sum()
print(f"Unresolved rows (no coords): {unresolved} / {len(df)} ({unresolved/len(df):.1%})")

Unresolved rows (no coords): 371374 / 1746661 (21.3%)


In [17]:
df

Unnamed: 0  State Code  County Code  Site Num  \
0                 0           4           13      3002   
1                 1           4           13      3002   
2                 2           4           13      3002   
3                 3           4           13      3002   
4                 4           4           13      3002   
...             ...         ...          ...       ...   
1746656       24599          56           21       100   
1746657       24600          56           21       100   
1746658       24601          56           21       100   
1746659       24602          56           21       100   
1746660       24603          56           21       100   

                                         Address    State    County  \
0        1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa   
1        1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa   
2        1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa   
3        1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa   
4        1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa   
...                                          ...      ...       ...   
1746656    NCore - North Cheyenne Soccer Complex  Wyoming   Laramie   
1746657    NCore - North Cheyenne Soccer Complex  Wyoming   Laramie   
1746658    NCore - North Cheyenne Soccer Complex  Wyoming   Laramie   
1746659    NCore - North Cheyenne Soccer Complex  Wyoming   Laramie   
1746660    NCore - North Cheyenne Soccer Complex  Wyoming   Laramie   

                  City  Date Local          NO2 Units  ...  SO2 1st Max Hour  \
0              Phoenix  2000-01-01  Parts per billion  ...                21   
1              Phoenix  2000-01-01  Parts per billion  ...                21   
2              Phoenix  2000-01-01  Parts per billion  ...                23   
3              Phoenix  2000-01-01  Parts per billion  ...                23   
4              Phoenix  2000-01-02  Parts per billion  ...                22   
...                ...         ...                ...  ...               ...   
1746656  Not in a city  2016-03-30  Parts per billion  ...                 2   
1746657  Not in a city  2016-03-31  Parts per billion  ...                 0   
1746658  Not in a city  2016-03-31  Parts per billion  ...                 0   
1746659  Not in a city  2016-03-31  Parts per billion  ...                 5   
1746660  Not in a city  2016-03-31  Parts per billion  ...                 5   

         SO2 AQI           CO Units   CO Mean CO 1st Max Value  \
0           13.0  Parts per million  1.145833            4.200   
1           13.0  Parts per million  0.878947            2.200   
2            NaN  Parts per million  1.145833            4.200   
3            NaN  Parts per million  0.878947            2.200   
4            4.0  Parts per million  0.850000            1.600   
...          ...                ...       ...              ...   
1746656      NaN  Parts per million  0.091667            0.100   
1746657      0.0  Parts per million  0.067714            0.127   
1746658      0.0  Parts per million  0.100000            0.100   
1746659      NaN  Parts per million  0.067714            0.127   
1746660      NaN  Parts per million  0.100000            0.100   

         CO 1st Max Hour  CO AQI  FirstToken          x           y  
0                     21     NaN        1645  33.646463 -112.095105  
1                     23    25.0        1645  33.646463 -112.095105  
2                     21     NaN        1645  33.646463 -112.095105  
3                     23    25.0        1645  33.646463 -112.095105  
4                     23     NaN        1645  33.646463 -112.095105  
...                  ...     ...         ...        ...         ...  
1746656                2     1.0       NCore        NaN         NaN  
1746657                0     NaN       NCore        NaN         NaN  
1746658                0     1.0       NCore        NaN         NaN  
17466

In [18]:
# Inspect unresolved rows (no coordinates found)
missing_df = df[df['x'].isna()].copy()
print(f"Missing coordinate rows: {len(missing_df)}")
missing_df.head(10)

Missing coordinate rows: 371374


Unnamed: 0  State Code  County Code  Site Num  \
6384        6384           6           13      1003   
6385        6385           6           13      1003   
6386        6386           6           13      1003   
6387        6387           6           13      1003   
6388        6388           6           13      1003   
6389        6389           6           13      1003   
6390        6390           6           13      1003   
6391        6391           6           13      1003   
6392        6392           6           13      1003   
6393        6393           6           13      1003   

                                            Address       State        County  \
6384  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6385  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6386  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6387  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6388  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6389  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6390  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6391  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6392  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   
6393  UNIT 759 EL PORTAL SHOPPING CENTER, San Pablo  California  Contra Costa   

           City  Date Local          NO2 Units  ...  SO2 1st Max Hour  \
6384  San Pablo  2000-01-01  Parts per billion  ...                 0   
6385  San Pablo  2000-01-01  Parts per billion  ...                 0   
6386  San Pablo  2000-01-01  Parts per billion  ...                 2   
6387  San Pablo  2000-01-01  Parts per billion  ...                 2   
6388  San Pablo  2000-01-02  Parts per billion  ...                 4   
6389  San Pablo  2000-01-02  Parts per billion  ...                 4   
6390  San Pablo  2000-01-02  Parts per billion  ...                 8   
6391  San Pablo  2000-01-02  Parts per billion  ...                 8   
6392  San Pablo  2000-01-03  Parts per billion  ...                15   
6393  San Pablo  2000-01-03  Parts per billion  ...                15   

      SO2 AQI           CO Units   CO Mean CO 1st Max Value  CO 1st Max Hour  \
6384      3.0  Parts per million  0.443478              0.7                2   
6385      3.0  Parts per million  0.433333              0.5                6   
6386      NaN  Parts per million  0.443478              0.7                2   
6387      NaN  Parts per million  0.433333              0.5                6   
6388      6.0  Parts per million  0.373913              0.7                8   
6389      6.0  Parts per million  0.400000              0.5                0   
6390      NaN  Parts per million  0.373913              0.7                8   
6391      NaN  Parts per million  0.400000              0.5                0   
6392     11.0  Parts per million  0.908696              1.6               18   
6393     11.0  Parts per million  0.754167              1.4               23   

      CO AQI  FirstToken   x   y  
6384     NaN        UNIT NaN NaN  
6385     6.0        UNIT NaN NaN  
6386     NaN        UNIT NaN NaN  
6387     6.0        UNIT NaN NaN  
6388     NaN        UNIT NaN NaN  
6389     6.0        UNIT NaN NaN  
6390     NaN        UNIT NaN NaN  
6391     6.0        UNIT NaN NaN  
6392     NaN        UNIT NaN NaN  
6393    16.0        UNIT NaN NaN  

[10 rows x 32 columns]

## Attempt 3 — simple city centroid fallback (City + County + State)

Let’s keep this clean and minimal:
1) Build a city-centroid dictionary keyed by (State, County, City)
2) Apply that dictionary to the DataFrame (non-destructive: lat_city/lon_city/coord_source_city)
3) Print a minimal coverage check (total, with city coord, without)

Notes:
- These are administrative centroids (not precise site locations). Use with caution.
- Keep original lon/lat intact; downstream can choose which to prefer.

In [20]:
# Column name configuration for Attempt 3
# Adjust these if your dataset uses different names
state_col, county_col, city_col = 'State', 'County', 'City'

# Sanity check: ensure these columns exist in df
_missing = [c for c in (state_col, county_col, city_col) if c not in df.columns]
if _missing:
    raise KeyError(f"Missing expected columns: {_missing}. Update state_col/county_col/city_col accordingly.")

In [21]:
# Minimal normalization helpers scoped to this cell
_def_suffixes = [
    ' County', ' county', ' Parish', ' parish', ' Borough', ' borough',
    ' Census Area', ' census area', ' Municipality', ' municipality',
    ' City and Borough', ' city and borough'
]

def _norm_city(s) -> str:
    return str(s).strip().lower()

def _norm_county(s) -> str:
    s = str(s).strip()
    for suf in _def_suffixes:
        if s.endswith(suf):
            s = s[:-len(suf)]
            break
    return s

# Build unique keys (State, County, City)
_city_keys_df = (
    df[[state_col, county_col, city_col]]
      .dropna()
      .assign(
          _state=lambda d: d[state_col].astype(str).str.strip(),
          _county=lambda d: d[county_col].map(_norm_county),
          _city=lambda d: d[city_col].map(_norm_city),
      )
      [["_state", "_county", "_city"]]
      .drop_duplicates()
)

city_key_to_coord: Dict[Tuple[str, str, str], Tuple[float, float]] = {}
_resolved = 0
_total = len(_city_keys_df)

for st, co, ci in _city_keys_df.itertuples(index=False):
    q = f"{ci}, {co} County, {st}, USA"
    try:
        loc = geolocator.geocode(q)
    except Exception:
        loc = None
    if loc is not None:
        city_key_to_coord[(st, co.lower(), ci)] = (loc.latitude, loc.longitude)
        _resolved += 1

print({
    'city_keys_total': _total,
    'city_keys_resolved': _resolved,
    'city_keys_unresolved': _total - _resolved,
})

{'city_keys_total': 177, 'city_keys_resolved': 131, 'city_keys_unresolved': 46}


### Apply centroids to DataFrame (non-destructive)

Adds lat_city, lon_city, and coord_source_city without touching existing lon/lat.

In [22]:
# Construct keys per row and map

def _key_from_row(row) -> tuple[str, str, str]:
    st = str(row[state_col]).strip()
    co = _norm_county(row[county_col]).lower()
    ci = _norm_city(row[city_col])
    return (st, co, ci)

_mask = df[[state_col, county_col, city_col]].notna().all(axis=1)
_keys = df.loc[_mask, [state_col, county_col, city_col]].apply(_key_from_row, axis=1)

# Map to coordinates
_latlon = _keys.map(lambda k: city_key_to_coord.get(k))

# Initialize new columns
for col in ('lat_city', 'lon_city', 'coord_source_city'):
    if col not in df.columns:
        df[col] = None

_hit_mask = _latlon.notna()
_hits = int(_hit_mask.sum())

# Assign values
_df_hits = df.loc[_mask].copy()
_df_hits = _df_hits.assign(_latlon=_latlon.values)
_df_hits = _df_hits.loc[_hit_mask]

if not _df_hits.empty:
    df.loc[_df_hits.index, 'lat_city'] = _df_hits['_latlon'].map(lambda t: t[0])
    df.loc[_df_hits.index, 'lon_city'] = _df_hits['_latlon'].map(lambda t: t[1])
    df.loc[_df_hits.index, 'coord_source_city'] = 'city_county_state'

print({'applied_rows': _hits})

{'applied_rows': 1517339}


### Minimal coverage check

Quick sanity metrics: total rows, with city coords, without city coords.

In [23]:
total_rows = int(len(df))
with_city = int(df['lat_city'].notna().sum()) if 'lat_city' in df.columns else 0
without_city = total_rows - with_city
print({'total_rows': total_rows, 'rows_with_city_coord': with_city, 'rows_without_city_coord': without_city})

{'total_rows': 1746661, 'rows_with_city_coord': 1517339, 'rows_without_city_coord': 229322}
